<a href="https://colab.research.google.com/github/nitsundon/Load-Forecast/blob/main/DataMining.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [1]:
import os
import drive.MyDrive.Libraries.wrldc_file_handler as wfh
import pandas as pd

In [2]:
folder_path='/content/drive/MyDrive/Libraries/data'
files = [f for f in os.listdir(folder_path) if os.path.isfile(os.path.join(folder_path, f))]
files.sort()
print(files)
df = pd.DataFrame()
for file in files:
  file_name=folder_path+"/"+file
  with open(file_name, 'r') as file:
    content = file.read()
  data = content
  df1=wfh.read_data(data)
  df1=df1.resample('15min').mean()
  df = pd.concat([df, df1])
df=df.reset_index()
df.columns=['datetime','demand']
df

['2025-04-03.json', '2025-04-04.json', '2025-04-05.json', '2025-04-06.json']


/usr/local/lib/python3.11/dist-packages/pandas/core/indexes/base.py:7588: FutureWarning: Dtype inference on a pandas object (Series, Index, ExtensionArray) is deprecated. The Index constructor will keep the original dtype in the future. Call `infer_objects` on the result to get the old behavior.
  return Index(sequences[0], name=names)
/usr/local/lib/python3.11/dist-packages/pandas/core/indexes/base.py:7588: FutureWarning: Dtype inference on a pandas object (Series, Index, ExtensionArray) is deprecated. The Index constructor will keep the original dtype in the future. Call `infer_objects` on the result to get the old behavior.
  return Index(sequences[0], name=names)
/usr/local/lib/python3.11/dist-packages/pandas/core/indexes/base.py:7588: FutureWarning: Dtype inference on a pandas object (Series, Index, ExtensionArray) is deprecated. The Index constructor will keep the original dtype in the future. Call `infer_objects` on the result to get the old behavior.
  return Index(sequences[0]

datetime        demand
0   2025-04-03 00:00:00  26416.100000
1   2025-04-03 00:15:00  26322.700000
2   2025-04-03 00:30:00  26246.833333
3   2025-04-03 00:45:00  26173.100000
4   2025-04-03 01:00:00  26105.500000
..                  ...           ...
340 2025-04-06 13:00:00  25732.909091
341 2025-04-06 13:15:00  25702.000000
342 2025-04-06 13:30:00  25666.909091
343 2025-04-06 13:45:00  25644.181818
344 2025-04-06 14:00:00  25524.750000

[345 rows x 2 columns]

In [6]:
scada_data_url="https://raw.githubusercontent.com/nitsundon/AIML/refs/heads/main/scada.csv"
df2= pd.read_csv(scada_data_url)
df2.columns=['datetime','demand']
df2["datetime"] = pd.to_datetime(df2["datetime"].copy(), errors="coerce")

df2=df2[~(df2['datetime']>'2024-04-03')]
df2 = pd.concat([df2, df])


datetime        demand
0   2020-01-01 00:00:00  13660.000000
1   2020-01-01 00:15:00  13637.000000
2   2020-01-01 00:30:00  13563.000000
3   2020-01-01 00:45:00      0.000000
4   2020-01-01 01:00:00      0.000000
..                  ...           ...
340 2025-04-06 13:00:00  25732.909091
341 2025-04-06 13:15:00  25702.000000
342 2025-04-06 13:30:00  25666.909091
343 2025-04-06 13:45:00  25644.181818
344 2025-04-06 14:00:00  25524.750000

[149530 rows x 2 columns]

In [8]:
df2['demand']=df2['demand'].fillna(0)
df2['lag'] = df2['demand'].shift(1)
df2['diff']=df2['demand']-df2['lag']

df2


datetime        demand           lag          diff
0   2020-01-01 00:00:00  13660.000000           NaN           NaN
1   2020-01-01 00:15:00  13637.000000  13660.000000    -23.000000
2   2020-01-01 00:30:00  13563.000000  13637.000000    -74.000000
3   2020-01-01 00:45:00      0.000000  13563.000000 -13563.000000
4   2020-01-01 01:00:00      0.000000      0.000000      0.000000
..                  ...           ...           ...           ...
340 2025-04-06 13:00:00  25732.909091  25762.400000    -29.490909
341 2025-04-06 13:15:00  25702.000000  25732.909091    -30.909091
342 2025-04-06 13:30:00  25666.909091  25702.000000    -35.090909
343 2025-04-06 13:45:00  25644.181818  25666.909091    -22.727273
344 2025-04-06 14:00:00  25524.750000  25644.181818   -119.431818

[149530 rows x 4 columns]

In [9]:

import plotly.express as px
fig = px.line(df2, x="datetime", y="diff",
              title="State Demand Over Time (15-Min Blocks)",
              labels={"Timestamp": "Time", "Demand_MW": "Demand (MW)"},
              template="plotly_dark")  # Optional: Use "seaborn" or "simple_white" theme

# Show interactive graph
fig.show()